# Input Source Codes

In [1]:
import os
import re
import nltk
import pandas as pd
import numpy as np
nltk.download('punkt')

from nltk.tokenize import word_tokenize
from sklearn.metrics import accuracy_score,precision_score,recall_score,f1_score

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\haydariday\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [2]:
source_codes = []
filenames = []
LOC = []
n_LOC = []
filenames_without_extension = []


tags_count = {}
function_dict = {}
function_token = {}

stop_condition = ('for', 'if', 'else', 'while','switch')

tags_count['LOC'] = 0
tags_count['SLOC'] = 0
tags_count['O'] = 0
tags_count['C'] = 0
tags_count['M'] = 0
tags_count['N'] = 0


sc_directory = 'Source_codes/postgre/'
py_directory = 'postgre.xls'

In [3]:
%%time

filenames = os.listdir(sc_directory)
for name in filenames :
    i = name.replace('.c','')
    filenames_without_extension.append(i)
filenames

Wall time: 0 ns


['list.c', 'outfuncs.c', 'pqformat.c', 'readfuncs.c', 'value.c']

In [4]:
%%time
i = 0
for files in filenames :
    function_dict[filenames_without_extension[i]] = {}
    with open(sc_directory+files,'r') as fh :
        source_codes.append([filenames_without_extension[i],fh.readlines()])
    i += 1

Wall time: 2 ms


In [5]:
%%time

for source_code in source_codes :
    i = 0
    for baris in source_code :
        if not (i % 2 == 0) :
            LOC.append(len(baris))
            tags_count['LOC'] += len(baris)
        i+=1
LOC

Wall time: 0 ns


[1275, 2820, 708, 1350, 75]

In [6]:
tags_count['LOC']

6228

In [7]:
source_codes[2]

['pqformat',
 ['/*-------------------------------------------------------------------------\n',
  ' *\n',
  ' * pqformat.c\n',
  ' *\t\tRoutines for formatting and parsing frontend/backend messages\n',
  ' *\n',
  ' * Outgoing messages are built up in a StringInfo buffer (which is expansible)\n',
  ' * and then sent in a single call to pq_putmessage.  This module provides data\n',
  ' * formatting/conversion routines that are needed to produce valid messages.\n',
  ' * Note in particular the distinction between "raw data" and "text"; raw data\n',
  ' * is message protocol characters and binary values that are not subject to\n',
  ' * character set conversion, while text is converted by character encoding\n',
  ' * rules.\n',
  ' *\n',
  ' * Incoming messages are similarly read into a StringInfo buffer, via\n',
  ' * pq_getmessage, and then parsed and converted from that using the routines\n',
  ' * in this module.\n',
  ' *\n',
  ' * These same routines support reading and writing of e

In [8]:
%%time
for code in source_codes :
    lines_update = []
    for i in range(1,len(code[1])+1) :
        lines_update.append([i,code[1][i-1]])
    code[1] = lines_update

Wall time: 3 ms


In [9]:
source_codes[2]

['pqformat',
 [[1,
   '/*-------------------------------------------------------------------------\n'],
  [2, ' *\n'],
  [3, ' * pqformat.c\n'],
  [4, ' *\t\tRoutines for formatting and parsing frontend/backend messages\n'],
  [5, ' *\n'],
  [6,
   ' * Outgoing messages are built up in a StringInfo buffer (which is expansible)\n'],
  [7,
   ' * and then sent in a single call to pq_putmessage.  This module provides data\n'],
  [8,
   ' * formatting/conversion routines that are needed to produce valid messages.\n'],
  [9,
   ' * Note in particular the distinction between "raw data" and "text"; raw data\n'],
  [10,
   ' * is message protocol characters and binary values that are not subject to\n'],
  [11,
   ' * character set conversion, while text is converted by character encoding\n'],
  [12, ' * rules.\n'],
  [13, ' *\n'],
  [14,
   ' * Incoming messages are similarly read into a StringInfo buffer, via\n'],
  [15,
   ' * pq_getmessage, and then parsed and converted from that using the 

# Data Pre-Processing 

## Remove whitespace

In [10]:
%%time
for code in source_codes :
    for i in range(len(code[1])) :
        code[1][i][1] = ' '.join(code[1][i][1].split())
        code[1][i][1] = code[1][i][1].replace('\t', '')
        code[1][i][1] = code[1][i][1].replace('\n', '')
        code[1][i][1] = code[1][i][1].replace('\\n\\', '')
        code[1][i][1] = code[1][i][1].replace('\\n', '')
        code[1][i][1] = code[1][i][1].replace('\\', ' \\ ')
        code[1][i][1] = code[1][i][1].replace('/', ' / ')
        code[1][i][1] = re.sub(r"^\s+","",code[1][i][1])

Wall time: 23 ms


In [11]:
source_codes[1]

['outfuncs',
 [[1,
   '/ *-------------------------------------------------------------------------'],
  [2, '*'],
  [3, '* outfuncs.c'],
  [4, '* Output functions for Postgres tree nodes.'],
  [5, '*'],
  [6,
   '* Portions Copyright (c) 1996-2009, PostgreSQL Global Development Group'],
  [7,
   '* Portions Copyright (c) 1994, Regents of the University of California'],
  [8, '*'],
  [9, '*'],
  [10, '* IDENTIFICATION'],
  [11,
   '* $PostgreSQL: pgsql / src / backend / nodes / outfuncs.c,v 1.360.2.3 2010 / 08 / 18 15:22:09 tgl Exp $'],
  [12, '*'],
  [13, '* NOTES'],
  [14, "* Every node type that can appear in stored rules' parsetrees *must*"],
  [15, '* have an output function defined here (as well as an input function'],
  [16, '* in readfuncs.c). For use in debugging, we also provide output'],
  [17,
   '* functions for nodes that appear in raw parsetrees, path, and plan trees.'],
  [18, '* These nodes however need not have input functions.'],
  [19, '*'],
  [20,
   '*------------

## Split Codes

In [12]:
%%time
for source_code in source_codes :
    i = 0
    for baris in source_code[1] :
        if not (baris[1] == '') :
            baris[1] = word_tokenize(baris[1])
        i += 1

Wall time: 435 ms


In [13]:
source_codes[1]

['outfuncs',
 [[1,
   ['/',
    '*',
    '--',
    '--',
    '--',
    '--',
    '--',
    '--',
    '--',
    '--',
    '--',
    '--',
    '--',
    '--',
    '--',
    '--',
    '--',
    '--',
    '--',
    '--',
    '--',
    '--',
    '--',
    '--',
    '--',
    '--',
    '--',
    '--',
    '--',
    '--',
    '--',
    '--',
    '--',
    '--',
    '--',
    '--',
    '--',
    '--',
    '-']],
  [2, ['*']],
  [3, ['*', 'outfuncs.c']],
  [4, ['*', 'Output', 'functions', 'for', 'Postgres', 'tree', 'nodes', '.']],
  [5, ['*']],
  [6,
   ['*',
    'Portions',
    'Copyright',
    '(',
    'c',
    ')',
    '1996-2009',
    ',',
    'PostgreSQL',
    'Global',
    'Development',
    'Group']],
  [7,
   ['*',
    'Portions',
    'Copyright',
    '(',
    'c',
    ')',
    '1994',
    ',',
    'Regents',
    'of',
    'the',
    'University',
    'of',
    'California']],
  [8, ['*']],
  [9, ['*']],
  [10, ['*', 'IDENTIFICATION']],
  [11,
   ['*',
    '$',
    'PostgreSQL',
    ':'

## Remove Comments

### Tag Comments

In [14]:
%%time

for source_code in source_codes :
    is_comment = False
    is_comment_line = False
    baris_index = 0
    while (baris_index < len(source_code[1])) :
        word_index = 0
        while (word_index < len(source_code[1][baris_index][1])) :
            tag = 'O'
            tags_count['O'] += 1
            #print(source_code[1][baris_index][1][word_index],end=' ')
            if not(is_comment or is_comment_line) : 
                out_of_bound = (len(source_code[1][baris_index][1])-word_index <= 1)
                #print('o',end=' ')
                if not(out_of_bound) :
                    if (source_code[1][baris_index][1][word_index] == '/') and (source_code[1][baris_index][1][word_index+1] == '*') :
                        is_comment = True
                        tag = 'C'
                        tags_count['O'] -= 1
                        #print('yes1',end=' ')
                    elif (source_code[1][baris_index][1][word_index] == '/') and (source_code[1][baris_index][1][word_index+1] == '/') :
                        is_comment_line = True
                        tag = 'C'
                        tags_count['O'] -= 1
                        #print('yes2',end=' ')
            elif (is_comment or is_comment_line) :
                tag = 'C'
                tags_count['O'] -= 1
                #print('yes3',end=' ')
                if (word_index > 0) and (is_comment) :
                    #print('no1',end=' ')
                    #print(source_code[1][baris_index][1][word_index-1], source_code[1][baris_index][1][word_index])
                    if (source_code[1][baris_index][1][word_index-1][0] == '*') and (source_code[1][baris_index][1][word_index] == '/') :
                        #print('no2',end=' ')
                        if (word_index > 1) :
                            #print('no3',end=' ')
                            if not (source_code[1][baris_index][1][word_index-2][0] == '/') :
                                is_comment = False
                                #print('no',end=' ')
                        else :
                            is_comment = False
            source_code[1][baris_index][1][word_index] = [source_code[1][baris_index][1][word_index], tag]
            word_index += 1
            #print('oh')
        baris_index += 1
        is_comment_line = False

Wall time: 43 ms


In [15]:
source_codes

[['list',
  [[1,
    [['/', 'C'],
     ['*', 'C'],
     ['--', 'C'],
     ['--', 'C'],
     ['--', 'C'],
     ['--', 'C'],
     ['--', 'C'],
     ['--', 'C'],
     ['--', 'C'],
     ['--', 'C'],
     ['--', 'C'],
     ['--', 'C'],
     ['--', 'C'],
     ['--', 'C'],
     ['--', 'C'],
     ['--', 'C'],
     ['--', 'C'],
     ['--', 'C'],
     ['--', 'C'],
     ['--', 'C'],
     ['--', 'C'],
     ['--', 'C'],
     ['--', 'C'],
     ['--', 'C'],
     ['--', 'C'],
     ['--', 'C'],
     ['--', 'C'],
     ['--', 'C'],
     ['--', 'C'],
     ['--', 'C'],
     ['--', 'C'],
     ['--', 'C'],
     ['--', 'C'],
     ['--', 'C'],
     ['--', 'C'],
     ['--', 'C'],
     ['--', 'C'],
     ['--', 'C'],
     ['-', 'C']]],
   [2, [['*', 'C']]],
   [3, [['*', 'C'], ['list.c', 'C']]],
   [4,
    [['*', 'C'],
     ['implementation', 'C'],
     ['for', 'C'],
     ['PostgreSQL', 'C'],
     ['generic', 'C'],
     ['linked', 'C'],
     ['list', 'C'],
     ['package', 'C']]],
   [5, [['*', 'C']]],
   [6, [['

### Removing Comments

In [16]:
%%time

for source_code in source_codes :
    baris_index = 0
    while (baris_index < len(source_code[1])) :
        word_index = 0
        while (word_index < len(source_code[1][baris_index][1])) :
            if (source_code[1][baris_index][1][word_index][1] == 'C') :
                source_code[1][baris_index][1].pop(word_index)
                tags_count['C'] += 1
            else :
                word_index += 1
        baris_index += 1

Wall time: 15.6 ms


## Remove Empty Baris

In [17]:
%%time

for source_code in source_codes :
    baris_index = 0   
    while (baris_index < len(source_code[1])) :
        if len(source_code[1][baris_index][1]) <= 0 :
            source_code[1].pop(baris_index)
        else :
            baris_index += 1
    n_LOC.append(len(source_code[1]))
    tags_count['SLOC'] += len(source_code[1])

Wall time: 0 ns


In [18]:
n_LOC

[738, 2254, 373, 873, 34]

In [19]:
tags_count['SLOC']

4272

In [20]:
source_codes[1]

['outfuncs',
 [[22,
   [['#', 'O'],
    ['include', 'O'],
    ['``', 'O'],
    ['postgres.h', 'O'],
    ["''", 'O']]],
  [24,
   [['#', 'O'], ['include', 'O'], ['<', 'O'], ['ctype.h', 'O'], ['>', 'O']]],
  [26,
   [['#', 'O'],
    ['include', 'O'],
    ['``', 'O'],
    ['lib', 'O'],
    ['/', 'O'],
    ['stringinfo.h', 'O'],
    ["''", 'O']]],
  [27,
   [['#', 'O'],
    ['include', 'O'],
    ['``', 'O'],
    ['nodes', 'O'],
    ['/', 'O'],
    ['plannodes.h', 'O'],
    ["''", 'O']]],
  [28,
   [['#', 'O'],
    ['include', 'O'],
    ['``', 'O'],
    ['nodes', 'O'],
    ['/', 'O'],
    ['relation.h', 'O'],
    ["''", 'O']]],
  [29,
   [['#', 'O'],
    ['include', 'O'],
    ['``', 'O'],
    ['utils', 'O'],
    ['/', 'O'],
    ['datum.h', 'O'],
    ["''", 'O']]],
  [40,
   [['#', 'O'],
    ['define', 'O'],
    ['WRITE_NODE_TYPE', 'O'],
    ['(', 'O'],
    ['nodelabel', 'O'],
    [')', 'O'],
    ['\\', 'O']]],
  [41,
   [['appendStringInfoString', 'O'],
    ['(', 'O'],
    ['str', 'O'],
   

# Tag Function

In [21]:
def check_is_function(source_code, index_word, index_baris, dict_function) :
    found = False #awali dengan kondisi tidak ditemukan
    
    #kondisi ketika pointer '{' merupakan urutan awal dari barisan token
    if (index_word <= 0) :
        try :
            index_baris = index_baris - 1
            index_word = len(source_code[1][index_baris][1]) - 1
        except :
            print("something went wrong, pointer can't get back to previous line")
    
    #kondisi ketika pointer '{' bukan urutan awal dari barisan
    else :
        index_word -=  1
        
    #kondisi ketika tidak menemukan token ')'
    #print('1.5',source_code[1][index_baris][1][index_word][0])
    if (not(source_code[1][index_baris][1][index_word][0] == ')')) :
        #print('why0')
        return False
    
    #cek apakah pointer berada pada baris awal dari source code
    if not(index_baris<=0) :
        #cek apakah pointer ada didalam macro
        if (source_code[1][index_baris-1][1][len(source_code[1][index_baris-1][1])-1][0]=='\\') :
            #print('why1')
            return False
    if (source_code[1][index_baris][1][0][0]=='#') :
        #print('why2')
        return False
    
    while (index_baris >= 0 and not(found)) :
        while (index_word >= 0 and not(found)) :
            #print('2',source_code[1][index_baris][1][index_word][0])
            if (source_code[1][index_baris][1][index_word][0] in stop_condition) :
                #print('why3')
                return False
            elif (source_code[1][index_baris][1][index_word][0] in (';','}')) :
                found = True;
            else :
                index_word -= 1
        if not(found) :
            index_baris = index_baris - 1
            index_word  = len(source_code[1][index_baris][1]) - 1
            
            # cek apakah baris macro
            #print('3',source_code[1][index_baris][1][index_word][0])
            if not(index_baris<=0) :
            #cek apakah pointer ada didalam macro
                #print('4',source_code[1][index_baris-1][1][len(source_code[1][index_baris-1][1])-1][0])
                if (source_code[1][index_baris-1][1][len(source_code[1][index_baris-1][1])-1][0]=='\\') :
                    found = True
            if (source_code[1][index_baris][1][0][0]=='#') :
                found = True

    if (len(source_code[1][index_baris][1]) - index_word <= 1 ) :
        index_baris += 1
        index_word = 0
    else :
        index_word += 1
        
    count = 0
    count_on = False
    is_named = False
    lines = []
    function_name = ''
    file_name = ''
    
    while (index_baris < len(source_code[1]) and (count>0 or not count_on)) :
        index_word = 0
        lines_temp = []
        lines_temp.append(source_code[1][index_baris][0])
        while (index_word < len(source_code[1][index_baris][1]) and (count>0 or not count_on)) :
            #print('g',source_code[1][index_baris][1][index_word])
            #print(index_baris)
            source_code[1][index_baris][1][index_word][1] = 'M'
            tags_count['M'] += 1
            tags_count['O'] -= 1
            lines_temp.append(source_code[1][index_baris][1][index_word][0])
            if (source_code[1][index_baris][1][index_word][0] == '{') :
                #print('yes0')
                count_on = True
                count += 1
            elif (not(is_named) and source_code[1][index_baris][1][index_word][0] == '(') :
                #print('yes1')
                if (index_word <= 0) :
                    #print('yes2')
                    source_code[1][index_baris-1][1][len(source_code[1][index_baris-1][1]) - 1][1] = 'N'
                    tags_count['M'] -= 1
                    tags_count['N'] += 1
                    function_name = source_code[1][index_baris-1][1][len(source_code[1][index_baris-1][1]) - 1][0]
                else :
                    #print('yes3')
                    source_code[1][index_baris][1][index_word-1][1] = 'N'
                    tags_count['M'] -= 1
                    tags_count['N'] += 1
                    function_name = source_code[1][index_baris][1][index_word-1][0]
                file_name = source_code[0]
                dict_function[file_name][function_name] = {}
                is_named = True
            elif (source_code[1][index_baris][1][index_word][0] == '}') :
                #print('yes4')
                count -= 1
            if (count>0 or not(count_on)) :
                index_word += 1
            #print(index_word < len(source_code[1][index_baris][1]) and (count>0 or not count_on))
        #print('final')
        lines.append(lines_temp)
        if (count>0 or not(count_on)) :
            index_baris += 1
    dict_function[file_name][function_name]['code'] = {}
    for line in lines :
        dict_function[file_name][function_name]['code'][line[0]] = []
        index = 1
        while (index<len(line)) :
            dict_function[file_name][function_name]['code'][line[0]].append(line[index])
            index += 1
    return True

In [22]:
%%time
jumlah = 0

for source_code in source_codes :
    baris_index = 0
    while (baris_index < len(source_code[1])) :
        word_index = 0
        while (word_index < len(source_code[1][baris_index][1])) :
            #print(baris_index,word_index)
            if not(source_code[1][baris_index][1][word_index][1] in ('M','N')) :    
                if (source_code[1][baris_index][1][word_index][0] == '{') :
                    if (check_is_function(source_code, word_index, baris_index,function_dict)) :
                        jumlah += 1
            word_index += 1
        baris_index += 1
#print('Jumlah :',jumlah)

Wall time: 53 ms


In [23]:
tags_count['M']

20756

In [24]:
tags_count['N']

290

In [25]:
tags_count['O']

1121

In [26]:
tags_count['C']

9012

In [27]:
tags_count['all'] = tags_count['M'] + tags_count['N'] + tags_count['O'] + tags_count['C']
tags_count['all']

31179

In [28]:
source_codes[1][1]

[[22,
  [['#', 'O'],
   ['include', 'O'],
   ['``', 'O'],
   ['postgres.h', 'O'],
   ["''", 'O']]],
 [24,
  [['#', 'O'], ['include', 'O'], ['<', 'O'], ['ctype.h', 'O'], ['>', 'O']]],
 [26,
  [['#', 'O'],
   ['include', 'O'],
   ['``', 'O'],
   ['lib', 'O'],
   ['/', 'O'],
   ['stringinfo.h', 'O'],
   ["''", 'O']]],
 [27,
  [['#', 'O'],
   ['include', 'O'],
   ['``', 'O'],
   ['nodes', 'O'],
   ['/', 'O'],
   ['plannodes.h', 'O'],
   ["''", 'O']]],
 [28,
  [['#', 'O'],
   ['include', 'O'],
   ['``', 'O'],
   ['nodes', 'O'],
   ['/', 'O'],
   ['relation.h', 'O'],
   ["''", 'O']]],
 [29,
  [['#', 'O'],
   ['include', 'O'],
   ['``', 'O'],
   ['utils', 'O'],
   ['/', 'O'],
   ['datum.h', 'O'],
   ["''", 'O']]],
 [40,
  [['#', 'O'],
   ['define', 'O'],
   ['WRITE_NODE_TYPE', 'O'],
   ['(', 'O'],
   ['nodelabel', 'O'],
   [')', 'O'],
   ['\\', 'O']]],
 [41,
  [['appendStringInfoString', 'O'],
   ['(', 'O'],
   ['str', 'O'],
   [',', 'O'],
   ['nodelabel', 'O'],
   [')', 'O']]],
 [44,
  [['#'

# Tokenization

In [29]:
syntax = ('for', 'while', 'case', 'if', 'do', 'else', 'break', 'continue', 'switch', 'goto', 'return')

def give_token(x) : 
    if x == 'for' :
        return 'A'
    elif x == 'break' :
        return 'B'
    elif x == 'case' :
        return 'C'
    elif x == 'do' :
        return 'D'
    elif x == 'else' :
        return 'E'
    elif x == 'continue' :
        return 'F'
    elif x == 'goto' :
        return 'G'
    elif x == 'while' :
        return 'H'
    elif x == 'if' :
        return 'I'
    elif x == 'switch' :
        return 'J'
    elif x == 'return' :
        return 'K'
    else :
        return False

In [30]:
%%time

is_in_comment1 = False
is_in_comment2 = False
is_in_comment3 = False
is_comment = False
dummy = {}
for file in list(function_dict) :
    for function in list(function_dict[file]) :
        dummy[function] = {}
        dummy[function]['token'] = ''
        for baris in list(function_dict[file][function]['code']) :
            for token in list(function_dict[file][function]['code'][baris]) :
                if (token == '"' and not(is_in_comment2) and not(is_in_comment3)) :
                    if not(is_in_comment1) : 
                        dummy[function]['token'] += 'T'
                        is_comment = not(is_comment)
                    is_in_comment1 = not(is_in_comment1)
                elif (token == "'" and not(is_in_comment1) and not(is_in_comment3)) :
                    if not(is_in_comment2) : 
                        dummy[function]['token'] += 'T'
                        is_comment = not(is_comment)
                    is_in_comment2 = not(is_in_comment2)
                elif ((token == "``" or token == "''") and not(is_in_comment1) and not(is_in_comment2)) :
                    if not(is_in_comment3) :
                        dummy[function]['token'] += 'T'
                        is_comment = not(is_comment)
                    is_in_comment3 = not(is_in_comment3)
                if (not(is_in_comment1 or is_in_comment2 or is_in_comment3 or is_comment)) :
                    if (re.search(r'^-[\w._]+$',token)) :
                        #print('1',re.findall(r'^-[\w._]+$',token)[0])
                        if (re.findall(r'[\w._]+$',token)[0] in syntax) :
                            dummy[function]['token'] += '-'
                            if not (give_token(re.findall(r'[\w._]+$',token)[0])) :
                                raise Exception('"{}" not found!'.format(re.findall(r'[\w._]+$',token)[0]))
                            dummy[function]['token'] += give_token(re.findall(r'[\w._]+$',token)[0])
                        else :
                            dummy[function]['token'] += 'T'
                    elif (re.search(r'^[\w._]+[^\w._]+$',token)) :
                        #print('2',re.findall(r'^[\w._]+[^\w._]+$',token)[0])
                        if (re.findall(r'^[\w._]+',token)[0] in syntax) :
                            if not (give_token(re.findall(r'^[\w._]+',token)[0])) :
                                raise Exception('"{}" not found!'.format(re.findall(r'^[\w._]+',token)[0]))
                            dummy[function]['token'] += give_token(re.findall(r'^[\w._]+',token)[0])
                        else :
                            dummy[function]['token'] += 'T'
                        dummy[function]['token'] += re.findall(r'[^\w._]+$',token)[0]
                    elif (re.search(r'^[^\w._]+[\w._]+$',token)) :
                        #print('3',re.findall(r'^[^\w._]+[\w._]+$',token)[0])
                        dummy[function]['token'] += re.findall(r'^[^\w._]+',token)[0]
                        if (re.findall(r'[\w._]+$',token)[0] in syntax) :
                            if not (give_token(re.findall(r'[\w._]+$',token)[0])) :
                                raise Exception('"{}" not found!'.format(re.findall(r'[\w._]+$',token)[0]))
                            dummy[function]['token'] += give_token(re.findall(r'[\w._]+$',token)[0])
                        else :
                            dummy[function]['token'] += 'T'
                    elif(re.search(r'^[\w.]+[^\w.]+[\w.]+$',token)) :
                        #print('4',re.findall(r'^[\w.]+[^\w.]+[\w.]+$',token)[0])
                        if (re.findall(r'^[\w._]+',token)[0] in syntax) :
                            if not (give_token(re.findall(r'^[\w._]+',token)[0])) :
                                raise Exception('"{}" not found!'.format(re.findall(r'^[\w._]+',token)[0]))
                            dummy[function]['token'] += give_token(re.findall(r'^[\w._]+',token)[0])
                        else :
                            dummy[function]['token'] += 'T'
                        dummy[function]['token'] += re.findall(r'[^\w._]+',token)[0]
                        if (re.findall(r'[\w._]+$',token)[0] in syntax) :
                            if not (give_token(re.findall(r'[\w._]+$',token)[0])) :
                                raise Exception('"{}" not found!'.format(re.findall(r'[\w._]+$',token)[0]))
                            dummy[function]['token'] += give_token(re.findall(r'[\w._]+$',token)[0])
                        else :
                            dummy[function]['token'] += 'T'
                    elif (re.search(r'^[\w._]+$',token)) :
                        #print('5',re.findall(r'^[\w._]+$',token)[0])
                        if (re.findall(r'^[\w._]+$',token)[0] in syntax) :
                            if not (give_token(re.findall(r'^[\w._]+$',token)[0])) :
                                raise Exception('"{}" not found!'.format(re.findall(r'^[\w._]+$',token)[0]))
                            dummy[function]['token'] += give_token(re.findall(r'^[\w._]+$',token)[0])
                        else :
                            #print('why :',re.findall(r'^[\w._]+$',token)[0])
                            dummy[function]['token'] += 'T'
                    else :
                        dummy[function]['token'] += token
                elif (not(is_in_comment1 or is_in_comment2 or is_in_comment3)) :
                    is_comment = not(is_comment)
                    
for file in list(function_dict) :
    for function in list(function_dict[file]) :
        function_dict[file][function]['token'] = dummy[function]['token']

Wall time: 30 ms


In [31]:
len(dummy)

290

In [32]:
dummy

{'check_list_invariants': {'token': 'TTT(T*T){I(T==T)K;T(T->T>T);T(T->T!=T);T(T->T!=T);T(T->T==T||T->T==T||T->T==T);I(T->T==T)T(T->T==T->T);I(T->T==T)T(T->T->T==T->T);T(T->T->T==T);}'},
 'new_list': {'token': 'TT*T(TT){T*T;T*T;T=(T*)T(T(*T));T->T=T;T=(T*)T(T(*T));T->T=T;T->T=T;T->T=T;T->T=T;KT;}'},
 'new_head_cell': {'token': 'TTT(T*T){T*T;T=(T*)T(T(*T));T->T=T->T;T->T=T;T->T++;}'},
 'new_tail_cell': {'token': 'TTT(T*T){T*T;T=(T*)T(T(*T));T->T=T;T->T->T=T;T->T=T;T->T++;}'},
 'lappend': {'token': 'T*T(T*T,T*T){T(T(T));I(T==T)T=T(T);ET(T);T(T->T)=T;T(T);KT;}'},
 'lappend_int': {'token': 'T*T(T*T,TT){T(T(T));I(T==T)T=T(T);ET(T);T(T->T)=T;T(T);KT;}'},
 'lappend_oid': {'token': 'T*T(T*T,TT){T(T(T));I(T==T)T=T(T);ET(T);T(T->T)=T;T(T);KT;}'},
 'add_new_cell': {'token': 'TT*T(T*T,T*T){T*T;T=(T*)T(T(*T));T->T=T->T;T->T=T;I(T->T==T)T->T=T;T->T++;KT;}'},
 'lappend_cell': {'token': 'T*T(T*T,T*T,T*T){T*T;T(T(T));T=T(T,T);T(T)=T;T(T);KT;}'},
 'lappend_cell_int': {'token': 'T*T(T*T,T*T,TT){T*T;T(T(T)

In [33]:
dummy

{'check_list_invariants': {'token': 'TTT(T*T){I(T==T)K;T(T->T>T);T(T->T!=T);T(T->T!=T);T(T->T==T||T->T==T||T->T==T);I(T->T==T)T(T->T==T->T);I(T->T==T)T(T->T->T==T->T);T(T->T->T==T);}'},
 'new_list': {'token': 'TT*T(TT){T*T;T*T;T=(T*)T(T(*T));T->T=T;T=(T*)T(T(*T));T->T=T;T->T=T;T->T=T;T->T=T;KT;}'},
 'new_head_cell': {'token': 'TTT(T*T){T*T;T=(T*)T(T(*T));T->T=T->T;T->T=T;T->T++;}'},
 'new_tail_cell': {'token': 'TTT(T*T){T*T;T=(T*)T(T(*T));T->T=T;T->T->T=T;T->T=T;T->T++;}'},
 'lappend': {'token': 'T*T(T*T,T*T){T(T(T));I(T==T)T=T(T);ET(T);T(T->T)=T;T(T);KT;}'},
 'lappend_int': {'token': 'T*T(T*T,TT){T(T(T));I(T==T)T=T(T);ET(T);T(T->T)=T;T(T);KT;}'},
 'lappend_oid': {'token': 'T*T(T*T,TT){T(T(T));I(T==T)T=T(T);ET(T);T(T->T)=T;T(T);KT;}'},
 'add_new_cell': {'token': 'TT*T(T*T,T*T){T*T;T=(T*)T(T(*T));T->T=T->T;T->T=T;I(T->T==T)T->T=T;T->T++;KT;}'},
 'lappend_cell': {'token': 'T*T(T*T,T*T,T*T){T*T;T(T(T));T=T(T,T);T(T)=T;T(T);KT;}'},
 'lappend_cell_int': {'token': 'T*T(T*T,T*T,TT){T*T;T(T(T)

In [34]:
i = 0
for file in function_dict :
    for function in function_dict[file] :
        function_token[file+'..'+function+'()']= function_dict[file][function]['token']

In [35]:
function_dict['outfuncs']['_outwindowagg']

KeyError: '_outwindowagg'

# Matching

In [36]:
import textdistance as td

## Seharusnya Code Clones

In [37]:
td.hamming.normalized_similarity(function_dict['audioop']['audioop_alaw2lin']['token'],function_dict['audioop']['audioop_reverse']['token'])

KeyError: 'audioop'

In [38]:
td.levenshtein.normalized_similarity(function_dict['audioop']['audioop_alaw2lin']['token'],function_dict['audioop']['audioop_reverse']['token'])

KeyError: 'audioop'

In [39]:
td.jaro_winkler(function_dict['audioop']['audioop_alaw2lin']['token'],function_dict['audioop']['audioop_reverse']['token'])

KeyError: 'audioop'

In [40]:
td.ratcliff_obershelp(function_dict['audioop']['audioop_reverse']['token'],function_dict['audioop']['audioop_alaw2lin']['token'])

KeyError: 'audioop'

## Seharusnya Bukan Code Clones

In [41]:
td.hamming.normalized_similarity(function_dict['audioop']['search']['token'],function_dict['audioop']['audioop_getsample']['token'])

KeyError: 'audioop'

In [42]:
td.levenshtein.normalized_similarity(function_dict['audioop']['search']['token'],function_dict['audioop']['audioop_getsample']['token'])

KeyError: 'audioop'

In [43]:
td.jaro_winkler(function_dict['audioop']['search']['token'],function_dict['audioop']['audioop_getsample']['token'])

KeyError: 'audioop'

In [ ]:
td.ratcliff_obershelp(function_dict['audioop']['search']['token'],function_dict['audioop']['audioop_getsample']['token'])

## Compare Functions

### ratcliff_obershelp

In [44]:
%%time
i = 0
key = list(function_token)
dummy = {}
is_clone10 = []
is_clone20 = []
is_clone30 = []
is_clone40 = []
is_clone50 = []
is_clone60 = []
is_clone70 = []
is_clone80 = []
is_clone90 = []
is_clone100 = []
while i < len(function_token)-1 :
    j = i+1
    while j < len(function_token) :
        if (key[i]<=key[j]) :
            func_to_compare = key[i]+'-'+key[j]
        else :
            func_to_compare = key[j]+'-'+key[i]
        dummy[func_to_compare] = td.ratcliff_obershelp(function_token[key[i]],function_token[key[j]])
        is_clone10.append(True)
        is_clone20.append(True)
        is_clone30.append(True)
        is_clone40.append(True)
        is_clone50.append(True)
        is_clone60.append(True)
        is_clone70.append(True)
        is_clone80.append(True)
        is_clone90.append(True)
        is_clone100.append(True)
        if (dummy[func_to_compare] < 1) :
            is_clone100[-1] = False
        if (dummy[func_to_compare] < 0.9) :
            is_clone90[-1] = False
        if (dummy[func_to_compare] < 0.8) :
            is_clone80[-1] = False
        if (dummy[func_to_compare] < 0.7) :
            is_clone70[-1] = False
        if (dummy[func_to_compare] < 0.6) :
            is_clone60[-1] = False
        if (dummy[func_to_compare] < 0.5) :
            is_clone50[-1] = False    
        if (dummy[func_to_compare] < 0.4) :
            is_clone40[-1] = False
        if (dummy[func_to_compare] < 0.3) :
            is_clone30[-1] = False
        if (dummy[func_to_compare] < 0.2) :
            is_clone20[-1] = False
        if (dummy[func_to_compare] < 0.1) :
            is_clone10[-1] = False
        j += 1
    i += 1

Wall time: 3.46 s


# Format Output

In [45]:

df = pd.DataFrame(data=dummy.items(),columns=['Method','Ratio'])
df['>10%'] = pd.DataFrame(is_clone10)
df['>20%'] = pd.DataFrame(is_clone20)
df['>30%'] = pd.DataFrame(is_clone30)
df['>40%'] = pd.DataFrame(is_clone40)
df['>50%'] = pd.DataFrame(is_clone50)
df['>60%'] = pd.DataFrame(is_clone60)
df['>70%'] = pd.DataFrame(is_clone70)
df['>80%'] = pd.DataFrame(is_clone80)
df['>90%'] = pd.DataFrame(is_clone90)
df['>100%'] = pd.DataFrame(is_clone100)

#df.set_index(['Method'], inplace=True)
df

Method     Ratio  >10%  \
0         list..check_list_invariants()-list..new_list()  0.389610  True   
1      list..check_list_invariants()-list..new_head_c...  0.373737  True   
2      list..check_list_invariants()-list..new_tail_c...  0.429268  True   
3          list..check_list_invariants()-list..lappend()  0.380488  True   
4      list..check_list_invariants()-list..lappend_int()  0.382353  True   
...                                                  ...       ...   ...   
41900           value..makeInteger()-value..makeString()  1.000000  True   
41901        value..makeBitString()-value..makeInteger()  1.000000  True   
41902             value..makeFloat()-value..makeString()  1.000000  True   
41903          value..makeBitString()-value..makeFloat()  1.000000  True   
41904         value..makeBitString()-value..makeString()  1.000000  True   

       >20%  >30%   >40%   >50%   >60%   >70%   >80%   >90%  >100%  
0      True  True  False  False  False  False  False  False  False  
1      True  True  False  False  False  False  False  False  False  
2      True  True   True  False  False  False  False  False  False  
3      True  True  False  False  False  False  False  False  False  
4      True  True  False  False  False  False  False  False  False  
...     ...   ...    ...    ...    ...    ...    ...    ...    ...  
41900  True  True   True   True   True   True   True   True   True  
41901  True  True   True   True   True   True   True   True   True  
41902  True  True   True   True   True   True   True   True   True  
41903  True  True   True   True   True   True   True   True   True  
41904  True  True   True   True   True   True   True   True   True  

[41905 rows x 12 columns]

In [46]:
df.sort_values(['Ratio'], ascending=False, axis=0, inplace=True)
df

Method  Ratio   >10%   >20%  \
41904         value..makeBitString()-value..makeString()    1.0   True   True   
29827  outfuncs.._outResultPath()-outfuncs.._outTarge...    1.0   True   True   
29729  outfuncs.._outCurrentOfExpr()-outfuncs.._outFk...    1.0   True   True   
29727  outfuncs.._outCurrentOfExpr()-outfuncs.._outRa...    1.0   True   True   
29726  outfuncs.._outCurrentOfExpr()-outfuncs.._outRa...    1.0   True   True   
...                                                  ...    ...    ...    ...   
26826  outfuncs.._outCoerceViaIO()-readfuncs.._readCo...    0.0  False  False   
26825  outfuncs.._outCoerceViaIO()-readfuncs.._readAr...    0.0  False  False   
26824  outfuncs.._outCoerceViaIO()-readfuncs.._readCo...    0.0  False  False   
26823  outfuncs.._outCoerceViaIO()-readfuncs.._readRe...    0.0  False  False   
20952   outfuncs.._outHashJoin()-readfuncs.._readParam()    0.0  False  False   

        >30%   >40%   >50%   >60%   >70%   >80%   >90%  >100%  
41904   True   True   True   True   True   True   True   True  
29827   True   True   True   True   True   True   True   True  
29729   True   True   True   True   True   True   True   True  
29727   True   True   True   True   True   True   True   True  
29726   True   True   True   True   True   True   True   True  
...      ...    ...    ...    ...    ...    ...    ...    ...  
26826  False  False  False  False  False  False  False  False  
26825  False  False  False  False  False  False  False  False  
26824  False  False  False  False  False  False  False  False  
26823  False  False  False  False  False  False  False  False  
20952  False  False  False  False  False  False  False  False  

[41905 rows x 12 columns]

In [68]:
df['Method']=df['Method'].str.lower()
df

Method  Ratio   >10%   >20%  \
41904         value..makebitstring()-value..makestring()    1.0   True   True   
29827  outfuncs.._outresultpath()-outfuncs.._outtarge...    1.0   True   True   
29729  outfuncs.._outcurrentofexpr()-outfuncs.._outfk...    1.0   True   True   
29727  outfuncs.._outcurrentofexpr()-outfuncs.._outra...    1.0   True   True   
29726  outfuncs.._outcurrentofexpr()-outfuncs.._outra...    1.0   True   True   
...                                                  ...    ...    ...    ...   
26826  outfuncs.._outcoerceviaio()-readfuncs.._readco...    0.0  False  False   
26825  outfuncs.._outcoerceviaio()-readfuncs.._readar...    0.0  False  False   
26824  outfuncs.._outcoerceviaio()-readfuncs.._readco...    0.0  False  False   
26823  outfuncs.._outcoerceviaio()-readfuncs.._readre...    0.0  False  False   
20952   outfuncs.._outhashjoin()-readfuncs.._readparam()    0.0  False  False   

        >30%   >40%   >50%   >60%   >70%   >80%   >90%  >100%  
41904   True   True   True   True   True   True   True   True  
29827   True   True   True   True   True   True   True   True  
29729   True   True   True   True   True   True   True   True  
29727   True   True   True   True   True   True   True   True  
29726   True   True   True   True   True   True   True   True  
...      ...    ...    ...    ...    ...    ...    ...    ...  
26826  False  False  False  False  False  False  False  False  
26825  False  False  False  False  False  False  False  False  
26824  False  False  False  False  False  False  False  False  
26823  False  False  False  False  False  False  False  False  
20952  False  False  False  False  False  False  False  False  

[41905 rows x 12 columns]

# Comparison

In [48]:
df_py = pd.read_excel(py_directory)
df_py

Unnamed: 0  Unnamed: 1  Student  \
0      outfuncs.._outjoinpathinfo()-outfuncs.._outbit...         NaN      0.0   
1      outfuncs.._outaggref()-outfuncs.._outbitmaphea...         NaN      NaN   
2      outfuncs.._outaggref()-outfuncs.._outjoinpathi...         NaN      NaN   
3      outfuncs.._outvaluesscan()-outfuncs.._outbitma...         NaN      NaN   
4      outfuncs.._outvaluesscan()-outfuncs.._outjoinp...         NaN      NaN   
...                                                  ...         ...      ...   
41333                                                NaN         NaN      NaN   
41334                                                NaN         NaN      NaN   
41335                                                NaN         NaN      NaN   
41336                                                NaN         NaN      NaN   
41337                                                NaN         NaN      NaN   

      Unnamed: 3    Expert  Nicad-30  Nicad-40  Nicad-50  MeCC_95_20  \
0            NaN  No Clone       0.0       0.0       0.0         0.0   
1            NaN       NaN       0.0       0.0       0.0         0.0   
2            NaN       NaN       0.0       0.0       0.0         0.0   
3            NaN       NaN       0.0       0.0       0.0         0.0   
4            NaN       NaN       0.0       0.0       0.0         0.0   
...          ...       ...       ...       ...       ...         ...   
41333     Type 1         0       NaN       NaN       NaN         NaN   
41334     Type 2        18       NaN       NaN       NaN         NaN   
41335     Type 3        10       NaN       NaN       NaN         NaN   
41336     Type 4         5       NaN       NaN       NaN         NaN   
41337   No Clone       601       NaN       NaN       NaN         NaN   

       MeCC_95_10  ...  MeCC_70_20  MeCC_70_10  MeCC_70_4  MeCC_60_20  \
0             0.0  ...         0.0         0.0        0.0         0.0   
1             0.0  ...         0.0         0.0        0.0         0.0   
2             0.0  ...         0.0         0.0        0.0         0.0   
3             0.0  ...         0.0         0.0        0.0         0.0   
4             0.0  ...         0.0         0.0        0.0         0.0   
...           ...  ...         ...         ...        ...         ...   
41333         NaN  ...         NaN         NaN        NaN         NaN   
41334         NaN  ...         NaN         NaN        NaN         NaN   
41335         NaN  ...         NaN         NaN        NaN         NaN   
41336         NaN  ...         NaN         NaN        NaN         NaN   
41337         NaN  ...         NaN         NaN        NaN         NaN   

       MeCC_60_10  MeCC_60_4  MeCC_50_20  MeCC_50_10  MeCC_50_4  Simcad  
0             0.0        0.0         0.0         0.0        0.0     0.0  
1             0.0        0.0         0.0         0.0        0.0     0.0  
2             0.0        0.0         0.0         0.0        0.0     0.0  
3             0.0        0.0         0.0         0.0        0.0     0.0  
4             0.0        0.0         0.0         0.0        0.0     0.0  
...           ...        ...         ...         ...        ...     ...  
41333         NaN        NaN         NaN         NaN        NaN     NaN  
41334         NaN        NaN         NaN         NaN        NaN     NaN  
41335         NaN        NaN         NaN         NaN        NaN     NaN  
41336         NaN        NaN         NaN         NaN        NaN     NaN  
41337         NaN        NaN         NaN         NaN        NaN     NaN  

[41338 rows x 27 columns]

In [49]:
df_py = df_py.dropna(subset=['Expert', 'Student'])
df_py

Unnamed: 0  Unnamed: 1  Student  \
0      outfuncs.._outjoinpathinfo()-outfuncs.._outbit...         NaN     0.00   
63      outfuncs.._outcreatestmt()-outfuncs.._outlimit()         NaN     0.25   
126    list..list_concat_unique()-readfuncs.._readsor...         NaN     0.00   
198    readfuncs.._readtargetentry()-outfuncs.._outli...         NaN     0.00   
261     readfuncs.._readrangevar()-outfuncs.._outlimit()         NaN     0.00   
...                                                  ...         ...      ...   
40509  readfuncs.._readscalararrayopexpr()-readfuncs....         NaN     0.75   
40572  readfuncs.._readscalararrayopexpr()-outfuncs.....         NaN     0.00   
40698  readfuncs.._readscalararrayopexpr()-outfuncs.....         NaN     0.75   
40986  outfuncs.._outrowcompareexpr()-outfuncs.._outa...         NaN     0.25   
41226   list..list_append_unique()-outfuncs.._outaexpr()         NaN     0.00   

      Unnamed: 3    Expert  Nicad-30  Nicad-40  Nicad-50  MeCC_95_20  \
0            NaN  No Clone       0.0       0.0       0.0         0.0   
63           NaN  No Clone       0.0       0.0       0.0         0.0   
126          NaN  No Clone       0.0       0.0       0.0         0.0   
198          NaN  No Clone       0.0       0.0       0.0         0.0   
261          NaN  No Clone       0.0       0.0       0.0         0.0   
...          ...       ...       ...       ...       ...         ...   
40509        NaN    Type 3       0.0       0.0       0.0         0.0   
40572        NaN  No Clone       0.0       0.0       0.0         0.0   
40698        NaN  No Clone       0.0       0.0       0.0         0.0   
40986        NaN  No Clone       0.0       0.0       0.0         0.0   
41226        NaN  No Clone       0.0       0.0       0.0         0.0   

       MeCC_95_10  ...  MeCC_70_20  MeCC_70_10  MeCC_70_4  MeCC_60_20  \
0             0.0  ...         0.0         0.0        0.0         0.0   
63            0.0  ...         0.0         0.0        0.0         0.0   
126           0.0  ...         0.0         0.0        0.0         0.0   
198           0.0  ...         0.0         0.0        0.0         0.0   
261           0.0  ...         0.0         0.0        0.0         0.0   
...           ...  ...         ...         ...        ...         ...   
40509         0.0  ...         0.0         0.0        0.0         0.0   
40572         0.0  ...         0.0         0.0        0.0         0.0   
40698         0.0  ...         0.0         0.0        0.0         0.0   
40986         0.0  ...         0.0         0.0        0.0         0.0   
41226         0.0  ...         0.0         0.0        0.0         0.0   

       MeCC_60_10  MeCC_60_4  MeCC_50_20  MeCC_50_10  MeCC_50_4  Simcad  
0             0.0        0.0         0.0         0.0        0.0     0.0  
63            0.0        0.0         0.0         0.0        0.0     0.0  
126           0.0        0.0         0.0         0.0        0.0     0.0  
198           0.0        0.0         0.0         0.0        0.0     0.0  
261           0.0        0.0         0.0         0.0        0.0     0.0  
...           ...        ...         ...         ...        ...     ...  
40509         0.0        0.0         0.0         0.0        0.0     0.0  
40572         0.0        0.0         0.0         0.0        0.0     0.0  
40698         0.0        0.0         0.0         0.0        0.0     0.0  
40986         0.0        0.0         0.0         0.0        0.0     0.0  
41226         0.0        0.0         0.0         0.0        0.0     0.0  

[657 rows x 27 columns]

In [50]:
df_py['Expert'].unique()

array(['No Clone', 'Unsure', 'Type 2', 'Type 3', 'Type 4', 'type 4',
       'Not Classified', 'type 2'], dtype=object)

In [51]:
for i in range(1,len(df_py.index)) :
    if (df_py.index[i]-df_py.index[i-1] > 4):
        print(df_py.index[i])

63
126
198
261
450
576
639
655
702
765
828
945
1008
1080
1143
1206
1260
1386
1458
1512
1575
1638
1701
1764
1827
1890
1953
2016
2079
2142
2205
2268
2331
2394
2466
2520
2529
2583
2592
2646
2655
2709
2718
2772
2781
2835
2844
2898
2907
2961
2970
3024
3033
3087
3096
3150
3159
3213
3222
3276
3285
3339
3348
3402
3411
3465
3474
3528
3537
3591
3600
3654
3663
3717
3726
3780
3786
3843
3906
3966
4026
4032
4086
4095
4146
4158
4206
4221
4266
4284
4326
4347
4386
4410
4446
4473
4506
4536
4566
4599
4626
4662
4686
4725
4746
4788
4806
4851
4866
4914
4926
4977
4986
5040
5046
5103
5166
5226
5286
5292
5346
5355
5406
5418
5466
5481
5526
5544
5586
5607
5646
5670
5706
5733
5766
5796
5826
5859
5886
5922
5946
5985
6006
6048
6066
6111
6126
6174
6186
6237
6246
6300
6306
6363
6426
6486
6546
6552
6606
6615
6666
6678
6726
6741
6786
6804
6846
6867
6906
6930
6966
6993
7026
7056
7086
7119
7146
7182
7206
7245
7266
7308
7326
7371
7386
7434
7446
7497
7506
7560
7566
7623
7686
7746
7806
7812
7866
7875
7926
7938
7986
8001
804

In [52]:
df_py = df_py[df_py.Expert != 'Unsure']
df_py = df_py[df_py.Expert != 'Not Classified']
df_py

Unnamed: 0  Unnamed: 1  Student  \
0      outfuncs.._outjoinpathinfo()-outfuncs.._outbit...         NaN     0.00   
63      outfuncs.._outcreatestmt()-outfuncs.._outlimit()         NaN     0.25   
126    list..list_concat_unique()-readfuncs.._readsor...         NaN     0.00   
198    readfuncs.._readtargetentry()-outfuncs.._outli...         NaN     0.00   
261     readfuncs.._readrangevar()-outfuncs.._outlimit()         NaN     0.00   
...                                                  ...         ...      ...   
40509  readfuncs.._readscalararrayopexpr()-readfuncs....         NaN     0.75   
40572  readfuncs.._readscalararrayopexpr()-outfuncs.....         NaN     0.00   
40698  readfuncs.._readscalararrayopexpr()-outfuncs.....         NaN     0.75   
40986  outfuncs.._outrowcompareexpr()-outfuncs.._outa...         NaN     0.25   
41226   list..list_append_unique()-outfuncs.._outaexpr()         NaN     0.00   

      Unnamed: 3    Expert  Nicad-30  Nicad-40  Nicad-50  MeCC_95_20  \
0            NaN  No Clone       0.0       0.0       0.0         0.0   
63           NaN  No Clone       0.0       0.0       0.0         0.0   
126          NaN  No Clone       0.0       0.0       0.0         0.0   
198          NaN  No Clone       0.0       0.0       0.0         0.0   
261          NaN  No Clone       0.0       0.0       0.0         0.0   
...          ...       ...       ...       ...       ...         ...   
40509        NaN    Type 3       0.0       0.0       0.0         0.0   
40572        NaN  No Clone       0.0       0.0       0.0         0.0   
40698        NaN  No Clone       0.0       0.0       0.0         0.0   
40986        NaN  No Clone       0.0       0.0       0.0         0.0   
41226        NaN  No Clone       0.0       0.0       0.0         0.0   

       MeCC_95_10  ...  MeCC_70_20  MeCC_70_10  MeCC_70_4  MeCC_60_20  \
0             0.0  ...         0.0         0.0        0.0         0.0   
63            0.0  ...         0.0         0.0        0.0         0.0   
126           0.0  ...         0.0         0.0        0.0         0.0   
198           0.0  ...         0.0         0.0        0.0         0.0   
261           0.0  ...         0.0         0.0        0.0         0.0   
...           ...  ...         ...         ...        ...         ...   
40509         0.0  ...         0.0         0.0        0.0         0.0   
40572         0.0  ...         0.0         0.0        0.0         0.0   
40698         0.0  ...         0.0         0.0        0.0         0.0   
40986         0.0  ...         0.0         0.0        0.0         0.0   
41226         0.0  ...         0.0         0.0        0.0         0.0   

       MeCC_60_10  MeCC_60_4  MeCC_50_20  MeCC_50_10  MeCC_50_4  Simcad  
0             0.0        0.0         0.0         0.0        0.0     0.0  
63            0.0        0.0         0.0         0.0        0.0     0.0  
126           0.0        0.0         0.0         0.0        0.0     0.0  
198           0.0        0.0         0.0         0.0        0.0     0.0  
261           0.0        0.0         0.0         0.0        0.0     0.0  
...           ...        ...         ...         ...        ...     ...  
40509         0.0        0.0         0.0         0.0        0.0     0.0  
40572         0.0        0.0         0.0         0.0        0.0     0.0  
40698         0.0        0.0         0.0         0.0        0.0     0.0  
40986         0.0        0.0         0.0         0.0        0.0     0.0  
41226         0.0        0.0         0.0         0.0        0.0     0.0  

[634 rows x 27 columns]

In [53]:
df_py = df_py.rename(columns={'Unnamed: 0':'Method'})

In [54]:
df_py = df_py[['Method','Expert']]
df_py

Method    Expert
0      outfuncs.._outjoinpathinfo()-outfuncs.._outbit...  No Clone
63      outfuncs.._outcreatestmt()-outfuncs.._outlimit()  No Clone
126    list..list_concat_unique()-readfuncs.._readsor...  No Clone
198    readfuncs.._readtargetentry()-outfuncs.._outli...  No Clone
261     readfuncs.._readrangevar()-outfuncs.._outlimit()  No Clone
...                                                  ...       ...
40509  readfuncs.._readscalararrayopexpr()-readfuncs....    Type 3
40572  readfuncs.._readscalararrayopexpr()-outfuncs.....  No Clone
40698  readfuncs.._readscalararrayopexpr()-outfuncs.....  No Clone
40986  outfuncs.._outrowcompareexpr()-outfuncs.._outa...  No Clone
41226   list..list_append_unique()-outfuncs.._outaexpr()  No Clone

[634 rows x 2 columns]

### Check if both result detected same methods

In [55]:
arr_comparable_methods = list(df_py['Method'])

arr_temp = []
for comparable_methods in arr_comparable_methods :
    temp = sorted(comparable_methods.split('-'))
    print(temp)
    arr_temp.append(temp)
arr_comparable_methods = arr_temp

['outfuncs.._outbitmapheapscan()', 'outfuncs.._outjoinpathinfo()']
['outfuncs.._outcreatestmt()', 'outfuncs.._outlimit()']
['list..list_concat_unique()', 'readfuncs.._readsortgroupclause()']
['outfuncs.._outlimit()', 'readfuncs.._readtargetentry()']
['outfuncs.._outlimit()', 'readfuncs.._readrangevar()']
['outfuncs.._outcasetestexpr()', 'outfuncs.._outsortgroupclause()']
['list..list_concat_unique_ptr()', 'readfuncs.._readquery()']
['readfuncs.._readfuncexpr()', 'readfuncs.._readquery()']
['pqformat..pq_copymsgbytes()', 'readfuncs.._readquery()']
['readfuncs.._readaggref()', 'readfuncs.._readwindowfunc()']
['list..list_delete()', 'outfuncs.._outlimit()']
['outfuncs.._outrowexpr()', 'readfuncs.._readjoinexpr()']
['list..lappend_int()', 'pqformat..pq_sendcountedtext()']
['pqformat..pq_sendcountedtext()', 'readfuncs.._readnullifexpr()']
['list..list_delete_first()', 'outfuncs.._outcasetestexpr()']
['outfuncs.._outnulltest()', 'outfuncs.._outsortgroupclause()']
['outfuncs.._outcasewhen()',

In [56]:
list0 = []
for row,col in df.iterrows() :
    methods = df.at[row,'Method'].split('-')
    for method in methods :
        print(method)
        if (method.lower() in list0) :
            print('no')
        else :
            list0.append(method.lower())
            print('yes')

value..makeBitString()
yes
value..makeString()
yes
outfuncs.._outResultPath()
yes
outfuncs.._outTargetEntry()
yes
outfuncs.._outCurrentOfExpr()
yes
outfuncs.._outFkConstraint()
yes
outfuncs.._outCurrentOfExpr()
no
outfuncs.._outRangeFunction()
yes
outfuncs.._outCurrentOfExpr()
no
outfuncs.._outRangeSubselect()
yes
outfuncs.._outCurrentOfExpr()
no
outfuncs.._outWindowDef()
yes
outfuncs.._outCurrentOfExpr()
no
outfuncs.._outSortBy()
yes
outfuncs.._outCurrentOfExpr()
no
outfuncs.._outResTarget()
yes
outfuncs.._outA_ArrayExpr()
yes
outfuncs.._outCurrentOfExpr()
no
outfuncs.._outJoin()
yes
outfuncs.._outPathKey()
yes
outfuncs.._outA_Indirection()
yes
outfuncs.._outCurrentOfExpr()
no
outfuncs.._outA_Indices()
yes
outfuncs.._outCurrentOfExpr()
no
outfuncs.._outA_Star()
yes
outfuncs.._outCurrentOfExpr()
no
outfuncs.._outInnerIndexscanInfo()
yes
outfuncs.._outJoin()
no
outfuncs.._outCurrentOfExpr()
no
outfuncs.._outParamRef()
yes
outfuncs.._outColumnRef()
yes
outfuncs.._outCurrentOfExpr()
no
ou

In [57]:
list1 = []
for comparable_methods in arr_comparable_methods :
    for method in comparable_methods :
        print(method)
        if (method.lower() in list1) :
            print('no')
        else :
            list1.append(method.lower())
            print('yes')

outfuncs.._outbitmapheapscan()
yes
outfuncs.._outjoinpathinfo()
yes
outfuncs.._outcreatestmt()
yes
outfuncs.._outlimit()
yes
list..list_concat_unique()
yes
readfuncs.._readsortgroupclause()
yes
outfuncs.._outlimit()
no
readfuncs.._readtargetentry()
yes
outfuncs.._outlimit()
no
readfuncs.._readrangevar()
yes
outfuncs.._outcasetestexpr()
yes
outfuncs.._outsortgroupclause()
yes
list..list_concat_unique_ptr()
yes
readfuncs.._readquery()
yes
readfuncs.._readfuncexpr()
yes
readfuncs.._readquery()
no
pqformat..pq_copymsgbytes()
yes
readfuncs.._readquery()
no
readfuncs.._readaggref()
yes
readfuncs.._readwindowfunc()
yes
list..list_delete()
yes
outfuncs.._outlimit()
no
outfuncs.._outrowexpr()
yes
readfuncs.._readjoinexpr()
yes
list..lappend_int()
yes
pqformat..pq_sendcountedtext()
yes
pqformat..pq_sendcountedtext()
no
readfuncs.._readnullifexpr()
yes
list..list_delete_first()
yes
outfuncs.._outcasetestexpr()
no
outfuncs.._outnulltest()
yes
outfuncs.._outsortgroupclause()
no
outfuncs.._outcasewh

#### Check if there are any differences

In [58]:
len(set(list1).difference(set(list0)))

0

In [59]:
set(list0).difference(set(list1))

{'list..check_list_invariants()',
 'list..lcons()',
 'list..list_concat()',
 'list..list_difference_oid()',
 'list..list_head()',
 'list..list_member_int()',
 'list..list_tail()',
 'list..list_union()',
 'outfuncs.._outa_indices()',
 'outfuncs.._outaggref()',
 'outfuncs.._outbitmapindexscan()',
 'outfuncs.._outboolexpr()',
 'outfuncs.._outcoalesceexpr()',
 'outfuncs.._outcolumnref()',
 'outfuncs.._outctescan()',
 'outfuncs.._outfuncexpr()',
 'outfuncs.._outjoin()',
 'outfuncs.._outmaterial()',
 'outfuncs.._outparamref()',
 'outfuncs.._outplannerparamitem()',
 'outfuncs.._outrestarget()',
 'outfuncs.._outselectstmt()',
 'outfuncs.._outtidscan()',
 'outfuncs.._outuniquepath()',
 'pqformat..pq_beginmessage()',
 'pqformat..pq_getmsgtext()',
 'readfuncs.._readarraycoerceexpr()',
 'readfuncs.._readcommontableexpr()',
 'readfuncs.._readintoclause()',
 'readfuncs.._readnulltest()',
 'readfuncs.._readrangetblref()',
 'readfuncs.._readrowexpr()',
 'readfuncs.._readrowmarkclause()',
 'readfuncs..

In [61]:
i = 0
list0_sorted = sorted(list0)
list1_sorted = sorted(list1)
while i < len(list0) :
    print(list0_sorted[i],end=' ')
    if i < len(list1) :
        print(list1_sorted[i])
    i+=1

list..add_new_cell() list..add_new_cell()
list..check_list_invariants() list..lappend()
list..lappend() list..lappend_cell()
list..lappend_cell() list..lappend_cell_int()
list..lappend_cell_int() list..lappend_cell_oid()
list..lappend_cell_oid() list..lappend_int()
list..lappend_int() list..lappend_oid()
list..lappend_oid() list..lcons_int()
list..lcons() list..lcons_oid()
list..lcons_int() list..length()
list..lcons_oid() list..list_append_unique()
list..length() list..list_append_unique_int()
list..list_append_unique() list..list_append_unique_oid()
list..list_append_unique_int() list..list_append_unique_ptr()
list..list_append_unique_oid() list..list_concat_unique()
list..list_append_unique_ptr() list..list_concat_unique_int()
list..list_concat() list..list_concat_unique_oid()
list..list_concat_unique() list..list_concat_unique_ptr()
list..list_concat_unique_int() list..list_copy()
list..list_concat_unique_oid() list..list_copy_tail()
list..list_concat_unique_ptr() list..list_delete

In [64]:
x = list(set(list0).difference(set(list1)))
for y in x :
    if not(y in list1) :
        print(y)

outfuncs.._outa_indices()
readfuncs.._readrangetblref()
outfuncs.._outplannerparamitem()
list..list_tail()
outfuncs.._outctescan()
outfuncs.._outjoin()
readfuncs.._readcommontableexpr()
readfuncs.._readrowmarkclause()
outfuncs.._outselectstmt()
outfuncs.._outmaterial()
readfuncs.._readintoclause()
readfuncs..parsenodestring()
outfuncs.._outtidscan()
outfuncs.._outparamref()
outfuncs.._outbitmapindexscan()
outfuncs.._outcoalesceexpr()
list..check_list_invariants()
outfuncs.._outrestarget()
list..lcons()
list..list_head()
readfuncs.._readarraycoerceexpr()
list..list_difference_oid()
outfuncs.._outuniquepath()
outfuncs.._outaggref()
list..list_member_int()
outfuncs.._outcolumnref()
pqformat..pq_beginmessage()
readfuncs.._readrowexpr()
outfuncs.._outfuncexpr()
readfuncs.._readnulltest()
list..list_concat()
outfuncs.._outboolexpr()
pqformat..pq_getmsgtext()
list..list_union()


In [65]:
patternDel = "fileB..methodB"
filter = df['Method'].str.contains(patternDel)

Method  Ratio   >10%   >20%  \
41904         value..makeBitString()-value..makeString()    1.0   True   True   
29827  outfuncs.._outResultPath()-outfuncs.._outTarge...    1.0   True   True   
29729  outfuncs.._outCurrentOfExpr()-outfuncs.._outFk...    1.0   True   True   
29727  outfuncs.._outCurrentOfExpr()-outfuncs.._outRa...    1.0   True   True   
29726  outfuncs.._outCurrentOfExpr()-outfuncs.._outRa...    1.0   True   True   
...                                                  ...    ...    ...    ...   
26826  outfuncs.._outCoerceViaIO()-readfuncs.._readCo...    0.0  False  False   
26825  outfuncs.._outCoerceViaIO()-readfuncs.._readAr...    0.0  False  False   
26824  outfuncs.._outCoerceViaIO()-readfuncs.._readCo...    0.0  False  False   
26823  outfuncs.._outCoerceViaIO()-readfuncs.._readRe...    0.0  False  False   
20952   outfuncs.._outHashJoin()-readfuncs.._readParam()    0.0  False  False   

        >30%   >40%   >50%   >60%   >70%   >80%   >90%  >100%  
41904   True   True   True   True   True   True   True   True  
29827   True   True   True   True   True   True   True   True  
29729   True   True   True   True   True   True   True   True  
29727   True   True   True   True   True   True   True   True  
29726   True   True   True   True   True   True   True   True  
...      ...    ...    ...    ...    ...    ...    ...    ...  
26826  False  False  False  False  False  False  False  False  
26825  False  False  False  False  False  False  False  False  
26824  False  False  False  False  False  False  False  False  
26823  False  False  False  False  False  False  False  False  
20952  False  False  False  False  False  False  False  False  

[41905 rows x 12 columns]

#### Get all the comparable method

In [55]:
for row in df_py['Method'] :
    key=row.split('-')
    if (key[0]<=key[1]) :
        new_key = key[0]+'-'+key[1]
    else :
        new_key = key[1]+'-'+key[0]
    df_py=df_py.replace(to_replace=row, value=new_key)

In [56]:
df_py=df_py.set_index('Method')
df_py

Expert
Method                                                      
outfuncs.._outbitmapheapscan()-outfuncs.._outjo...  No Clone
outfuncs.._outcreatestmt()-outfuncs.._outlimit()    No Clone
list..list_concat_unique()-readfuncs.._readsort...  No Clone
outfuncs.._outlimit()-readfuncs.._readtargetent...  No Clone
outfuncs.._outlimit()-readfuncs.._readrangevar()    No Clone
...                                                      ...
readfuncs.._readscalararrayopexpr()-readfuncs.....    Type 3
outfuncs.._outa_arrayexpr()-readfuncs.._readsca...  No Clone
outfuncs.._outbitmapandpath()-readfuncs.._reads...  No Clone
outfuncs.._outarrayexpr()-outfuncs.._outrowcomp...  No Clone
list..list_append_unique()-outfuncs.._outaexpr()    No Clone

[634 rows x 1 columns]

In [ ]:
df = df.set_index('Method')

In [60]:
df

Ratio   >10%   >20%  \
Method                                                                       
audioop..audioop_alaw2lin()-audioop..audioop_ul...  1.000000   True   True   
cmathmodule..c_acosh()-cmathmodule..c_asinh()       1.000000   True   True   
cmathmodule..c_cosh()-cmathmodule..c_sinh()         1.000000   True   True   
audioop..audioop_lin2alaw()-audioop..audioop_li...  1.000000   True   True   
cmathmodule..c_cos()-cmathmodule..c_sinh()          1.000000   True   True   
...                                                      ...    ...    ...   
fcntlmodule..all_ins()-grpmodule..initgrp()         0.046125  False  False   
audioop..search()-fcntlmodule..all_ins()            0.045028  False  False   
audioop..audioop_ratecv()-cmathmodule..c_prodi()    0.042831  False  False   
cmathmodule..c_prodi()-fcntlmodule..all_ins()       0.040619  False  False   
fcntlmodule..all_ins()-fpectlmodule..sigfpe_han...  0.036329  False  False   

                                                     >30%   >40%   >50%  \
Method                                                                    
audioop..audioop_alaw2lin()-audioop..audioop_ul...   True   True   True   
cmathmodule..c_acosh()-cmathmodule..c_asinh()        True   True   True   
cmathmodule..c_cosh()-cmathmodule..c_sinh()          True   True   True   
audioop..audioop_lin2alaw()-audioop..audioop_li...   True   True   True   
cmathmodule..c_cos()-cmathmodule..c_sinh()           True   True   True   
...                                                   ...    ...    ...   
fcntlmodule..all_ins()-grpmodule..initgrp()         False  False  False   
audioop..search()-fcntlmodule..all_ins()            False  False  False   
audioop..audioop_ratecv()-cmathmodule..c_prodi()    False  False  False   
cmathmodule..c_prodi()-fcntlmodule..all_ins()       False  False  False   
fcntlmodule..all_ins()-fpectlmodule..sigfpe_han...  False  False  False   

                                                     >60%   >70%   >80%  \
Method                                                                    
audioop..audioop_alaw2lin()-audioop..audioop_ul...   True   True   True   
cmathmodule..c_acosh()-cmathmodule..c_asinh()        True   True   True   
cmathmodule..c_cosh()-cmathmodule..c_sinh()          True   True   True   
audioop..audioop_lin2alaw()-audioop..audioop_li...   True   True   True   
cmathmodule..c_cos()-cmathmodule..c_sinh()           True   True   True   
...                                                   ...    ...    ...   
fcntlmodule..all_ins()-grpmodule..initgrp()         False  False  False   
audioop..search()-fcntlmodule..all_ins()            False  False  False   
audioop..audioop_ratecv()-cmathmodule..c_prodi()    False  False  False   
cmathmodule..c_prodi()-fcntlmodule..all_ins()       False  False  False   
fcntlmodule..all_ins()-fpectlmodule..sigfpe_han...  False  False  False   

                                                     >90%  >100%  
Method                                                            
audioop..audioop_alaw2lin()-audioop..audioop_ul...   True   True  
cmathmodule..c_acosh()-cmathmodule..c_asinh()        True   True  
cmathmodule..c_cosh()-cmathmodule..c_sinh()          True   True  
audioop..audioop_lin2alaw()-audioop..audioop_li...   True   True  
cmathmodule..c_cos()-cmathmodule..c_sinh()           True   True  
...                                                   ...    ...  
fcntlmodule..all_ins()-grpmodule..initgrp()         False  False  
audioop..search()-fcntlmodule..all_ins()            False  False  
audioop..audioop_ratecv()-cmathmodule..c_prodi()    False  False  
cmathmodule..c_prodi()-fcntlmodule..all_ins()       False  False  
fcntlmodule..all_ins()-fpectlmodule..sigfpe_han...  False  False  

[3003 rows x 11 columns]

In [62]:
df_final=pd.concat([df, df_py], axis=1)
df_final = df_final.dropna(subset=['Expert'])
df_final['Expert'] = df_final['Expert'].replace(to_replace=r'^No Clone$', value= False, regex=True)
df_final['Expert'] = df_final['Expert'].replace(to_replace=r'^Type.*$', value= True, regex=True)
df_final['Expert'] = df_final['Expert'].replace(to_replace=r'^type.*$', value= True, regex=True)
df_final

Ratio   >10%   >20%  \
audioop..audioop_avgpp()-audioop..audioop_maxpp()   0.949939   True   True   
audioop..audioop_avg()-audioop..audioop_minmax()    0.920097   True   True   
audioop..audioop_max()-audioop..audioop_rms()       0.908654   True   True   
audioop..audioop_avg()-audioop..audioop_max()       0.904177   True   True   
audioop..audioop_mul()-audioop..audioop_tomono()    0.878866   True   True   
...                                                      ...    ...    ...   
audioop..audioop_ratecv()-cmathmodule..c_sinh()     0.071560  False  False   
cmathmodule..c_acos()-fcntlmodule..all_ins()        0.070142  False  False   
cmathmodule..math_error()-fcntlmodule..all_ins()    0.069943  False  False   
audioop..audioop_ratecv()-fcntlmodule..conv_des...  0.067890  False  False   
fcntlmodule..all_ins()-fcntlmodule..ins()           0.061972  False  False   

                                                     >30%   >40%   >50%  \
audioop..audioop_avgpp()-audioop..audioop_maxpp()    True   True   True   
audioop..audioop_avg()-audioop..audioop_minmax()     True   True   True   
audioop..audioop_max()-audioop..audioop_rms()        True   True   True   
audioop..audioop_avg()-audioop..audioop_max()        True   True   True   
audioop..audioop_mul()-audioop..audioop_tomono()     True   True   True   
...                                                   ...    ...    ...   
audioop..audioop_ratecv()-cmathmodule..c_sinh()     False  False  False   
cmathmodule..c_acos()-fcntlmodule..all_ins()        False  False  False   
cmathmodule..math_error()-fcntlmodule..all_ins()    False  False  False   
audioop..audioop_ratecv()-fcntlmodule..conv_des...  False  False  False   
fcntlmodule..all_ins()-fcntlmodule..ins()           False  False  False   

                                                     >60%   >70%   >80%  \
audioop..audioop_avgpp()-audioop..audioop_maxpp()    True   True   True   
audioop..audioop_avg()-audioop..audioop_minmax()     True   True   True   
audioop..audioop_max()-audioop..audioop_rms()        True   True   True   
audioop..audioop_avg()-audioop..audioop_max()        True   True   True   
audioop..audioop_mul()-audioop..audioop_tomono()     True   True   True   
...                                                   ...    ...    ...   
audioop..audioop_ratecv()-cmathmodule..c_sinh()     False  False  False   
cmathmodule..c_acos()-fcntlmodule..all_ins()        False  False  False   
cmathmodule..math_error()-fcntlmodule..all_ins()    False  False  False   
audioop..audioop_ratecv()-fcntlmodule..conv_des...  False  False  False   
fcntlmodule..all_ins()-fcntlmodule..ins()           False  False  False   

                                                     >90%  >100%  Expert  
audioop..audioop_avgpp()-audioop..audioop_maxpp()    True  False    True  
audioop..audioop_avg()-audioop..audioop_minmax()     True  False    True  
audioop..audioop_max()-audioop..audioop_rms()        True  False    True  
audioop..audioop_avg()-audioop..audioop_max()        True  False    True  
audioop..audioop_mul()-audioop..audioop_tomono()    False  False    True  
...                                                   ...    ...     ...  
audioop..audioop_ratecv()-cmathmodule..c_sinh()     False  False   False  
cmathmodule..c_acos()-fcntlmodule..all_ins()        False  False   False  
cmathmodule..math_error()-fcntlmodule..all_ins()    False  False   False  
audioop..audioop_ratecv()-fcntlmodule..conv_des...  False  False   False  
fcntlmodule..all_ins()-fcntlmodule..ins()           False  False   False  

[545 rows x 12 columns]

In [116]:
for ratio in ['>10%','>20%','>30%','>40%','>50%','>60%','>70%','>80%','>90%','>100%'] :
    comparison_column = np.where((df_final[ratio] == df_final['Expert']) , True, False)
    df_final[ratio+' Result'] = comparison_column

In [117]:
df_final

Ratio   >10%   >20%  \
audioop..audioop_avgpp()-audioop..audioop_maxpp()   0.949939   True   True   
audioop..audioop_avg()-audioop..audioop_minmax()    0.920097   True   True   
audioop..audioop_max()-audioop..audioop_rms()       0.908654   True   True   
audioop..audioop_avg()-audioop..audioop_max()       0.904177   True   True   
audioop..audioop_mul()-audioop..audioop_tomono()    0.878866   True   True   
...                                                      ...    ...    ...   
audioop..audioop_ratecv()-cmathmodule..c_sinh()     0.071560  False  False   
cmathmodule..c_acos()-fcntlmodule..all_ins()        0.070142  False  False   
cmathmodule..math_error()-fcntlmodule..all_ins()    0.069943  False  False   
audioop..audioop_ratecv()-fcntlmodule..conv_des...  0.067890  False  False   
fcntlmodule..all_ins()-fcntlmodule..ins()           0.061972  False  False   

                                                     >30%   >40%   >50%  \
audioop..audioop_avgpp()-audioop..audioop_maxpp()    True   True   True   
audioop..audioop_avg()-audioop..audioop_minmax()     True   True   True   
audioop..audioop_max()-audioop..audioop_rms()        True   True   True   
audioop..audioop_avg()-audioop..audioop_max()        True   True   True   
audioop..audioop_mul()-audioop..audioop_tomono()     True   True   True   
...                                                   ...    ...    ...   
audioop..audioop_ratecv()-cmathmodule..c_sinh()     False  False  False   
cmathmodule..c_acos()-fcntlmodule..all_ins()        False  False  False   
cmathmodule..math_error()-fcntlmodule..all_ins()    False  False  False   
audioop..audioop_ratecv()-fcntlmodule..conv_des...  False  False  False   
fcntlmodule..all_ins()-fcntlmodule..ins()           False  False  False   

                                                     >60%   >70%   >80%  \
audioop..audioop_avgpp()-audioop..audioop_maxpp()    True   True   True   
audioop..audioop_avg()-audioop..audioop_minmax()     True   True   True   
audioop..audioop_max()-audioop..audioop_rms()        True   True   True   
audioop..audioop_avg()-audioop..audioop_max()        True   True   True   
audioop..audioop_mul()-audioop..audioop_tomono()     True   True   True   
...                                                   ...    ...    ...   
audioop..audioop_ratecv()-cmathmodule..c_sinh()     False  False  False   
cmathmodule..c_acos()-fcntlmodule..all_ins()        False  False  False   
cmathmodule..math_error()-fcntlmodule..all_ins()    False  False  False   
audioop..audioop_ratecv()-fcntlmodule..conv_des...  False  False  False   
fcntlmodule..all_ins()-fcntlmodule..ins()           False  False  False   

                                                     >90%  ...  >10% Result  \
audioop..audioop_avgpp()-audioop..audioop_maxpp()    True  ...         True   
audioop..audioop_avg()-audioop..audioop_minmax()     True  ...         True   
audioop..audioop_max()-audioop..audioop_rms()        True  ...         True   
audioop..audioop_avg()-audioop..audioop_max()        True  ...         True   
audioop..audioop_mul()-audioop..audioop_tomono()    False  ...         True   
...                                                   ...  ...          ...   
audioop..audioop_ratecv()-cmathmodule..c_sinh()     False  ...         True   
cmathmodule..c_acos()-fcntlmodule..all_ins()        False  ...         True   
cmathmodule..math_error()-fcntlmodule..all_ins()    False  ...         True   
audioop..audioop_ratecv()-fcntlmodule..conv_des...  False  ...         True   
fcntlmodule..all_ins()-fcntlmodule..ins()           False  ...         True   

                                                   >20% Result  >30% Result  \
audioop..audioop_avgpp()-audioop..audioop_maxpp()         True         True   
audioop..audioop_avg()-audioop..audioop_minmax()          True         True   
audioop..audioop_max()-audioop..audioop_rms()             True         True   
audioop..audioop_avg()-audioop..audioop_max()      

In [89]:
confusion_matrix = pd.crosstab(df_final['Expert'], df_final['>10%'], rownames=['Actual'], colnames=['Predicted'])
print(">10% Accuracy :",accuracy_score(df_final['Expert'],df_final['>10%']))
print(">10% Precision :",precision_score(df_final['Expert'],df_final['>10%']))
print(">10% Recall :",recall_score(df_final['Expert'],df_final['>10%']))
print(">10% F1 :",f1_score(df_final['Expert'],df_final['>10%']))
confusion_matrix

>10% Accuracy : 0.05504587155963303
>10% Precision : 0.02830188679245283
>10% Recall : 1.0
>10% F1 : 0.055045871559633024


Predicted  False  True 
Actual                 
False         15    515
True           0     15

In [90]:
confusion_matrix = pd.crosstab(df_final['Expert'], df_final['>20%'], rownames=['Actual'], colnames=['Predicted'])
print(">20% Accuracy :",accuracy_score(df_final['Expert'],df_final['>20%']))
print(">20% Precision :",precision_score(df_final['Expert'],df_final['>20%']))
print(">20% Recall :",recall_score(df_final['Expert'],df_final['>20%']))
print(">20% F1 :",f1_score(df_final['Expert'],df_final['>20%']))
confusion_matrix

>20% Accuracy : 0.24036697247706423
>20% Precision : 0.03496503496503497
>20% Recall : 1.0
>20% F1 : 0.06756756756756757


Predicted  False  True 
Actual                 
False        116    414
True           0     15

In [91]:
confusion_matrix = pd.crosstab(df_final['Expert'], df_final['>30%'], rownames=['Actual'], colnames=['Predicted'])
print(">30% Accuracy :",accuracy_score(df_final['Expert'],df_final['>30%']))
print(">30% Precision :",precision_score(df_final['Expert'],df_final['>30%']))
print(">30% Recall :",recall_score(df_final['Expert'],df_final['>30%']))
print(">30% F1 :",f1_score(df_final['Expert'],df_final['>30%']))
confusion_matrix

>30% Accuracy : 0.43853211009174314
>30% Precision : 0.04672897196261682
>30% Recall : 1.0
>30% F1 : 0.08928571428571429


Predicted  False  True 
Actual                 
False        224    306
True           0     15

In [92]:
confusion_matrix = pd.crosstab(df_final['Expert'], df_final['>40%'], rownames=['Actual'], colnames=['Predicted'])
print(">40% Accuracy :",accuracy_score(df_final['Expert'],df_final['>40%']))
print(">40% Precision :",precision_score(df_final['Expert'],df_final['>40%']))
print(">40% Recall :",recall_score(df_final['Expert'],df_final['>40%']))
print(">40% F1 :",f1_score(df_final['Expert'],df_final['>40%']))
confusion_matrix

>40% Accuracy : 0.6513761467889908
>40% Precision : 0.07317073170731707
>40% Recall : 1.0
>40% F1 : 0.13636363636363635


Predicted  False  True 
Actual                 
False        340    190
True           0     15

In [93]:
confusion_matrix = pd.crosstab(df_final['Expert'], df_final['>50%'], rownames=['Actual'], colnames=['Predicted'])
print(">50% Accuracy :",accuracy_score(df_final['Expert'],df_final['>50%']))
print(">50% Precision :",precision_score(df_final['Expert'],df_final['>50%']))
print(">50% Recall :",recall_score(df_final['Expert'],df_final['>50%']))
print(">50% F1 :",f1_score(df_final['Expert'],df_final['>50%']))
confusion_matrix

>50% Accuracy : 0.8091743119266055
>50% Precision : 0.12605042016806722
>50% Recall : 1.0
>50% F1 : 0.22388059701492538


Predicted  False  True 
Actual                 
False        426    104
True           0     15

In [95]:
confusion_matrix = pd.crosstab(df_final['Expert'], df_final['>60%'], rownames=['Actual'], colnames=['Predicted'])
print(">60% Accuracy :",accuracy_score(df_final['Expert'],df_final['>60%']))
print(">60% Precision :",precision_score(df_final['Expert'],df_final['>60%']))
print(">60% Recall :",recall_score(df_final['Expert'],df_final['>60%']))
print(">60% F1 :",f1_score(df_final['Expert'],df_final['>60%']))
confusion_matrix

>60% Accuracy : 0.9119266055045872
>60% Precision : 0.23809523809523808
>60% Recall : 1.0
>60% F1 : 0.3846153846153846


Predicted  False  True 
Actual                 
False        482     48
True           0     15

In [96]:
confusion_matrix = pd.crosstab(df_final['Expert'], df_final['>70%'], rownames=['Actual'], colnames=['Predicted'])
print(">70% Accuracy :",accuracy_score(df_final['Expert'],df_final['>70%']))
print(">70% Precision :",precision_score(df_final['Expert'],df_final['>70%']))
print(">70% Recall :",recall_score(df_final['Expert'],df_final['>70%']))
print(">70% F1 :",f1_score(df_final['Expert'],df_final['>70%']))
confusion_matrix

>70% Accuracy : 0.9761467889908257
>70% Precision : 0.5357142857142857
>70% Recall : 1.0
>70% F1 : 0.6976744186046512


Predicted  False  True 
Actual                 
False        517     13
True           0     15

In [97]:
confusion_matrix = pd.crosstab(df_final['Expert'], df_final['>80%'], rownames=['Actual'], colnames=['Predicted'])
print(">80% Accuracy :",accuracy_score(df_final['Expert'],df_final['>80%']))
print(">80% Precision :",precision_score(df_final['Expert'],df_final['>80%']))
print(">80% Recall :",recall_score(df_final['Expert'],df_final['>80%']))
print(">80% F1 :",f1_score(df_final['Expert'],df_final['>80%']))
confusion_matrix

>80% Accuracy : 0.9944954128440368
>80% Precision : 0.9285714285714286
>80% Recall : 0.8666666666666667
>80% F1 : 0.896551724137931


Predicted  False  True 
Actual                 
False        529      1
True           2     13

In [98]:
confusion_matrix = pd.crosstab(df_final['Expert'], df_final['>90%'], rownames=['Actual'], colnames=['Predicted'])
print(">90% Accuracy :",accuracy_score(df_final['Expert'],df_final['>90%']))
print(">90% Precision :",precision_score(df_final['Expert'],df_final['>90%']))
print(">90% Recall :",recall_score(df_final['Expert'],df_final['>90%']))
print(">90% F1 :",f1_score(df_final['Expert'],df_final['>90%']))
confusion_matrix

>90% Accuracy : 0.9798165137614679
>90% Precision : 1.0
>90% Recall : 0.26666666666666666
>90% F1 : 0.4210526315789474


Predicted  False  True 
Actual                 
False        530      0
True          11      4

In [99]:
confusion_matrix = pd.crosstab(df_final['Expert'], df_final['>100%'], rownames=['Actual'], colnames=['Predicted'])
print(">100% Accuracy :",accuracy_score(df_final['Expert'],df_final['>100%']))
print(">100% Precision :",precision_score(df_final['Expert'],df_final['>100%']))
print(">100% Recall :",recall_score(df_final['Expert'],df_final['>100%']))
print(">100% F1 :",f1_score(df_final['Expert'],df_final['>100%']))
confusion_matrix

>100% Accuracy : 0.9724770642201835
>100% Precision : 0.0
>100% Recall : 0.0
>100% F1 : 0.0


C:\Users\haydariday\Anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1245: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


Predicted  False
Actual          
False        530
True          15